In [0]:
from pyspark.sql import SparkSession

In [0]:
spark = SparkSession.builder \
        .appName('mllib') \
        .getOrCreate()

In [0]:
storage_account_name = "chengyangbde"
storage_account_access_key = "89Y9ZLqYL8RN3MNqcTnvMGNnPOuArORjnNDbWLhkXzkRTYaD/GfvSmaY8sdFz+wonSC4llRg5osD+AStJmIHug=="
blob_container_name = "bde-2"

In [0]:
# Q2
mount_points = [mount.mountPoint for mount in dbutils.fs.mounts()]

if f"/mnt/{blob_container_name}/" not in mount_points:
    dbutils.fs.mount(
      source = f'wasbs://{blob_container_name}@{storage_account_name}.blob.core.windows.net',
      mount_point = f'/mnt/{blob_container_name}/',
      extra_configs = {'fs.azure.account.key.' + storage_account_name + '.blob.core.windows.net': storage_account_access_key}
    )
else:
    print(f"/mnt/{blob_container_name}/ is already mounted. Skipping.")


/mnt/bde-2/ is already mounted. Skipping.


In [0]:
# Q3 Define paths
green_path = "/mnt/bde-2/green/"
yellow_path = "/mnt/bde-2/yellow/"

# Count rows for green taxi
green_df = spark.read.parquet(green_path)
green_taxi_rows = green_df.count()
print(f"Total rows for Green Taxi: {green_taxi_rows}")

# Count rows for yellow taxi
yellow_df = spark.read.parquet(yellow_path)
yellow_taxi_rows = yellow_df.count()
print(f"Total rows for Yellow Taxi: {yellow_taxi_rows}")

Total rows for Green Taxi: 66200401
Total rows for Yellow Taxi: 663055251


In [0]:
# Q4, Read the location referential CSV into a DataFrame
location_df = spark.read.csv("/mnt/bde-2/taxi_zone_lookup.csv", header=True, inferSchema=True)
location_df.show()

+----------+-------------+--------------------+------------+
|LocationID|      Borough|                Zone|service_zone|
+----------+-------------+--------------------+------------+
|         1|          EWR|      Newark Airport|         EWR|
|         2|       Queens|         Jamaica Bay|   Boro Zone|
|         3|        Bronx|Allerton/Pelham G...|   Boro Zone|
|         4|    Manhattan|       Alphabet City| Yellow Zone|
|         5|Staten Island|       Arden Heights|   Boro Zone|
|         6|Staten Island|Arrochar/Fort Wad...|   Boro Zone|
|         7|       Queens|             Astoria|   Boro Zone|
|         8|       Queens|        Astoria Park|   Boro Zone|
|         9|       Queens|          Auburndale|   Boro Zone|
|        10|       Queens|        Baisley Park|   Boro Zone|
|        11|     Brooklyn|          Bath Beach|   Boro Zone|
|        12|    Manhattan|        Battery Park| Yellow Zone|
|        13|    Manhattan|   Battery Park City| Yellow Zone|
|        14|     Brookly

In [0]:
# Q5 Path for 2015 Green taxi data
green_2015_path = "/mnt/bde-2/green/green_taxi_2015.parquet"

# Read the 2015 Green taxi parquet file
green_2015_df = spark.read.parquet(green_2015_path)

# Write the DataFrame to CSV format and store it in the bde-2 container
csv_save_path = "/mnt/bde-2/green/green_taxi_2015.csv"
green_2015_df.write.csv(csv_save_path, header=True)


---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-3989595250661421>, line 9
      7 # Write the DataFrame to CSV format and store it in the bde-2 container
      8 csv_save_path = "/mnt/bde-2/green/green_taxi_2015.csv"
----> 9 green_2015_df.write.csv(csv_save_path, header=True)

File /databricks/spark/python/pyspark/instrumentation_utils.py:48, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     46 start = time.perf_counter()
     47 try:
---> 48     res = func(*args, **kwargs)
     49     logger.log_success(
     50         module_name, class_name, function_name, time.perf_counter() - start, signature
     51     )
     52     return res

File /databricks/spark/python/pyspark/sql/readwriter.py:1864, in DataFrameWriter.csv(self, path, mode, compression, sep, quote, escape, header, nullValue, escapeQuotes, quoteAll, dateFormat, timestampFormat, ignoreLeadingWhiteSpace

In [0]:
from pyspark.sql.functions import col

# Q6 Cleaning Yellow Taxi data

# 1. Remove trips finishing before starting time
cleaned_yellow_df = yellow_df.filter(col("tpep_dropoff_datetime") >= col("tpep_pickup_datetime"))

# 2. Remove trips with unrealistic dates
cleaned_yellow_df = cleaned_yellow_df.filter((col("tpep_pickup_datetime").between("2015-01-01", "2022-12-31")) & 
                                             (col("tpep_dropoff_datetime").between("2015-01-01", "2022-12-31")))

# 3 & 4. Remove trips with negative or high speed
# Calculate trip duration in hours
cleaned_yellow_df = cleaned_yellow_df.withColumn("trip_duration_hours", 
                                                 (col("tpep_dropoff_datetime").cast("long") - col("tpep_pickup_datetime").cast("long")) / 3600.0)

# Calculate speed
cleaned_yellow_df = cleaned_yellow_df.withColumn("speed", col("trip_distance") / col("trip_duration_hours"))

# Filter out trips with negative speed or speed higher than limits
cleaned_yellow_df = cleaned_yellow_df.filter((col("speed") >= 0) & (col("speed") <= 65))  

# 5. Remove trips with very short or long durations
cleaned_yellow_df = cleaned_yellow_df.filter((col("trip_duration_hours") >= 1/60) & (col("trip_duration_hours") <= 3))

# 6. Remove trips with very short or long distances
cleaned_yellow_df = cleaned_yellow_df.filter((col("trip_distance") >= 0.1) & (col("trip_distance") <= 100))

# 7. Remove trips with negative fares
cleaned_yellow_df = cleaned_yellow_df.filter(col("fare_amount") >= 0)

cleaned_yellow_df_count = cleaned_yellow_df.count()
print(f"Cleaned rows for Yellow Taxi: {cleaned_yellow_df_count}")


Cleaned rows for Yellow Taxi: 653201824


In [0]:
from pyspark.sql.functions import col

# Cleaning Green Taxi data

# 1. Remove trips finishing before starting time
cleaned_green_df = green_df.filter(col("lpep_dropoff_datetime") >= col("lpep_pickup_datetime"))

# 2. Remove trips with unrealistic dates
cleaned_green_df = cleaned_green_df.filter((col("lpep_pickup_datetime").between("2015-01-01", "2022-12-31")) & 
                                          (col("lpep_dropoff_datetime").between("2015-01-01", "2022-12-31")))

# 3 & 4. Remove trips with negative or high speed
# Calculate trip duration in hours
cleaned_green_df = cleaned_green_df.withColumn("trip_duration_hours", 
                                              (col("lpep_dropoff_datetime").cast("long") - col("lpep_pickup_datetime").cast("long")) / 3600.0)

# Calculate speed
cleaned_green_df = cleaned_green_df.withColumn("speed", col("trip_distance") / col("trip_duration_hours"))

# Filter out trips with negative speed or speed higher than limits
cleaned_green_df = cleaned_green_df.filter((col("speed") >= 0) & (col("speed") <= 65))  

# 5. Remove trips with very short or long durations
cleaned_green_df = cleaned_green_df.filter((col("trip_duration_hours") >= 1/60) & (col("trip_duration_hours") <= 3))

# 6. Remove trips with very short or long distances
cleaned_green_df = cleaned_green_df.filter((col("trip_distance") >= 0.1) & (col("trip_distance") <= 100))

# 7. Remove trips with negative fares
cleaned_green_df = cleaned_green_df.filter(col("fare_amount") >= 0)

cleaned_green_df_count = cleaned_green_df.count()
print(f"Cleaned rows for Green Taxi: {cleaned_green_df_count}")


Cleaned rows for Green Taxi: 64131380


In [0]:
print("Columns in cleaned_green_df:")
print(cleaned_green_df.columns)



Columns in cleaned_green_df:
['VendorID', 'lpep_pickup_datetime', 'lpep_dropoff_datetime', 'store_and_fwd_flag', 'RatecodeID', 'PULocationID', 'DOLocationID', 'passenger_count', 'trip_distance', 'fare_amount', 'extra', 'mta_tax', 'tip_amount', 'tolls_amount', 'ehail_fee', 'improvement_surcharge', 'total_amount', 'payment_type', 'trip_type', 'congestion_surcharge', 'trip_duration_hours', 'speed']


In [0]:
from pyspark.sql.functions import lit

# Add a TaxiColor column to cleaned_green_df and cleaned_yellow_df
cleaned_green_df = cleaned_green_df.withColumn("TaxiColor", lit("green"))
cleaned_yellow_df = cleaned_yellow_df.withColumn("TaxiColor", lit("yellow"))

# Align schemas of cleaned green and yellow dataframes
for column in cleaned_green_df.columns:
    if column not in cleaned_yellow_df.columns:
        cleaned_yellow_df = cleaned_yellow_df.withColumn(column, lit(None))

for column in cleaned_yellow_df.columns:
    if column not in cleaned_green_df.columns:
        cleaned_green_df = cleaned_green_df.withColumn(column, lit(None))

# Order columns to make it consistent between dataframes
cleaned_green_df = cleaned_green_df.select(*cleaned_yellow_df.columns)
cleaned_yellow_df = cleaned_yellow_df.select(*cleaned_green_df.columns)

# Combine the cleaned dataframes
combined_df = cleaned_green_df.union(cleaned_yellow_df)




In [0]:
# Q8 Read the location data
location_df = spark.read.csv("/mnt/bde-2/taxi_zone_lookup.csv", header=True, inferSchema=True)

# Join with pick-up and drop-off locations
combined_df = combined_df.join(location_df, combined_df.PULocationID == location_df.LocationID, "left_outer") \
                         .drop('LocationID') \
                         .withColumnRenamed('Borough', 'PUBorough') \
                         .withColumnRenamed('Zone', 'PUZone') \
                         .withColumnRenamed('service_zone', 'PUServiceZone')

combined_df = combined_df.join(location_df, combined_df.DOLocationID == location_df.LocationID, "left_outer") \
                         .drop('LocationID') \
                         .withColumnRenamed('Borough', 'DOBorough') \
                         .withColumnRenamed('Zone', 'DOZone') \
                         .withColumnRenamed('service_zone', 'DOServiceZone')


In [0]:
# Q9, Write the combined dataframe to a parquet file
parquet_path = "/mnt/bde-2/combined_data4.parquet"
combined_df.write.parquet(parquet_path)

# Load it as a table or view
spark.sql(f"CREATE OR REPLACE TEMPORARY VIEW combined_view AS SELECT * FROM parquet.`{parquet_path}`")


DataFrame[]

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col
# handle NAH value
spark = SparkSession.builder \
    .appName("Taxi Data Processing") \
    .getOrCreate()

df = spark.read.parquet("/mnt/bde-2/combined_data4.parquet")

# Define default values for columns, including datetime columns
default_values = {
    "trip_distance": 0.0,
    "passenger_count": 1,
    "RatecodeID": 1,
    "PULocationID": 0,
    "DOLocationID": 0,  
}

# Fill null values in the combined dataframe
df = df.fillna(default_values)

# Save the cleaned and processed dataframe back to Parquet format
parquet_path_cleaned = "/mnt/bde-2/combined_data_cleaned6.parquet"
df.write.parquet(parquet_path_cleaned)

print(f"Data saved to {parquet_path_cleaned}")


Data saved to /mnt/bde-2/combined_data_cleaned6.parquet


In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW combined_view AS SELECT * FROM parquet.`/mnt/bde-2/combined_data_cleaned6.parquet`;

In [0]:
%sql
SELECT 
    YEAR(COALESCE(lpep_pickup_datetime, tpep_pickup_datetime)) AS Year, 
    MONTH(COALESCE(lpep_pickup_datetime, tpep_pickup_datetime)) AS Month, 
    DAYOFWEEK(COALESCE(lpep_pickup_datetime, tpep_pickup_datetime)) AS DayOfWeek, 
    HOUR(COALESCE(lpep_pickup_datetime, tpep_pickup_datetime)) AS HourOfDay,
    
    COUNT(*) AS TotalTrips,

    AVG(passenger_count) AS AvgPassengers,

    AVG(total_amount) AS AvgAmountPerTrip,

    CASE WHEN SUM(passenger_count) > 0 THEN
        SUM(total_amount) / SUM(passenger_count)
    ELSE
        0
    END AS AvgAmountPerPassenger

FROM combined_view 
WHERE passenger_count > 0 
GROUP BY 
    YEAR(COALESCE(lpep_pickup_datetime, tpep_pickup_datetime)), 
    MONTH(COALESCE(lpep_pickup_datetime, tpep_pickup_datetime)), 
    DAYOFWEEK(COALESCE(lpep_pickup_datetime, tpep_pickup_datetime)), 
    HOUR(COALESCE(lpep_pickup_datetime, tpep_pickup_datetime))
ORDER BY Year, Month, DayOfWeek, HourOfDay;



Year Month DayOfWeek HourOfDay TotalTrips AvgPassengers AvgAmountPerTrip AvgAmountPerPassenger 2015 1 1 0 118955 1.7439704089781851 14.681031482497353 8.41816547282999 2015 1 1 1 103781 1.7278788988350469 14.787082703001001 8.557939282070404 2015 1 1 2 85883 1.7301677864070888 14.925590396234943 8.626672229997885 2015 1 1 3 65125 1.724898272552783 15.38519232245324 8.919478074312027 2015 1 1 4 40240 1.7148359840954275 16.186308648108803 9.438983551915053 2015 1 1 5 18608 1.6527300085984522 18.97073463026676 11.47842329453092 2015 1 1 6 17767 1.539483311757753 20.283867844880795 13.17576338110548 2015 1 1 7 23734 1.5315581023004972 17.00192297969068 11.101062998623895 2015 1 1 8 36021 1.5943199800116599 14.225476805194884 8.92259833881706 2015 1 1 9 54858 1.6369353603849939 13.349278136275656 8.15504292920645 2015 1 1 10 75782 1.674606106991106 13.112245651997537 7.830047673453979 2015 1 1 11 90073 1.6905398954181607 12.994335705480042 7.686500472836134 2015 1 1 12 97968 1.6999836681365343 13.212740894984956 7.772275194542501 2015 1 1 13 99813 1.6974041457525573 13.761700880647032 8.107498096480539 2015 1 1 14 98863 1.6945571143906213 14.608633968218802 8.620915662363027 2015 1 1 15 94654 1.6906417055803242 14.903356857607077 8.815207153837129 2015 1 1 16 91594 1.6913444112059741 15.058905495991803 8.903512138757355 2015 1 1 17 93572 1.6836019322019407 14.648133202238547 8.700473028728721 2015 1 1 18 96702 1.693501685590784 14.37956484870956 8.491024822153157 2015 1 1 19 87088 1.6878904097005327 59.47973624377052 35.239098404690544 2015 1 1 20 77891 1.6718747993991603 14.905804778469468 8.91562261948462 2015 1 1 21 70745 1.668174429288289 15.482882182483511 9.281332881411652 2015 1 1 22 65117 1.667736535774068 16.203647434614837 9.71595158290037 2015 1 1 23 54493 1.6489273851687372 16.98592553171726 10.301196817092745 2015 1 2 0 38896 1.63944878650761 17.092753753598007 10.425915035753796 2015 1 2 1 24755 1.624075944253686 16.442249242576942 10.124064272211527 2015 1 2 2 16979 1.6105777725425525 15.632738088227388 9.70629196226186 2015 1 2 3 12727 1.6152274691600534 16.600637227941146 10.277584764314199 2015 1 2 4 12690 1.6130811662726556 19.811413711584592 12.281721543722936 2015 1 2 5 17849 1.544120118774161 21.014337497899298 13.609263451979412 2015 1 2 6 42102 1.5249156809652749 16.162272813641398 10.598797701005111 2015 1 2 7 71999 1.5667995388824845 14.540767649547483 9.280553950072417 2015 1 2 8 89651 1.5940368763315524 14.312849271058813 8.978995080714686 2015 1 2 9 85458 1.5917643754826933 14.32064897376159 8.99671408302434 2015 1 2 10 76299 1.60103015766917 14.099447830243646 8.806484851459679 2015 1 2 11 76705 1.6313799621928167 14.014787562737125 8.59075622327687 2015 1 2 12 81495 1.6352046137799865 13.593561690897866 8.31306466257736 2015 1 2 13 82377 1.6329315221481724 14.008430629905929 8.57870060067026 2015 1 2 14 83654 1.6485165084753868 14.8853146293035 9.02952111960955 2015 1 2 15 79778 1.6632906315024192 15.053782747119785 9.050602740136872 2015 1 2 16 70059 1.6553761829315292 15.376960133598624 9.289103161051495 2015 1 2 17 78504 1.644221950473861 14.838015132983553 9.024338307068136 2015 1 2 18 90824 1.636681934290496 14.147100215798499 8.643768785736178 2015 1 2 19 85775 1.6344039638589332 14.055612124741659 8.599839718667502 2015 1 2 20 75214 1.640279735155689 14.4404085675509 8.803625539018363 2015 1 2 21 68074 1.6447983077239474 15.188114258010481 9.234028383107724 2015 1 2 22 57631 1.654942652391942 15.88486196664741 9.59843650394079 2015 1 2 23 41673 1.644590022316608 16.595134739518166 10.090742686217853 2015 1 3 0 29937 1.628185856966296 49.557082874035785 30.436993824754513 2015 1 3 1 16818 1.6038173385658223 15.767382566298735 9.83115856597383 2015 1 3 2 10618 1.593614616688642 15.577924279525677 9.775214230837635 2015 1 3 3 6911 1.609318477789032 15.865860222832893 9.858744830066367 2015 1 3 4 7475 1.5757859531772576 18.78626220735796 11.921836318872634 2015 1 3 5 13276 1.5221452244652003 18.904

In [0]:
%sql
WITH TripCalculations AS (
    SELECT 
        TaxiColor,
        trip_duration_hours * 60 AS TripDurationMinutes, 
        trip_distance * 1.60934 AS TripDistanceKM,
        (trip_distance * 1.60934) / trip_duration_hours AS SpeedKMH  
    FROM combined_view
)

SELECT 
    TaxiColor,
    ROUND(AVG(TripDurationMinutes), 2) AS AverageDuration,
    PERCENTILE_APPROX(TripDurationMinutes, 0.5) AS MedianDuration,
    MIN(TripDurationMinutes) AS MinimumDuration,
    MAX(TripDurationMinutes) AS MaximumDuration,
    
    ROUND(AVG(TripDistanceKM), 2) AS AverageDistance,
    PERCENTILE_APPROX(TripDistanceKM, 0.5) AS MedianDistance,
    MIN(TripDistanceKM) AS MinimumDistance,
    MAX(TripDistanceKM) AS MaximumDistance,
    
    ROUND(AVG(SpeedKMH), 2) AS AverageSpeed,
    PERCENTILE_APPROX(SpeedKMH, 0.5) AS MedianSpeed,
    MIN(SpeedKMH) AS MinimumSpeed,
    MAX(SpeedKMH) AS MaximumSpeed

FROM TripCalculations
GROUP BY TaxiColor;


TaxiColor AverageDuration MedianDuration MinimumDuration MaximumDuration AverageDistance MedianDistance MinimumDistance MaximumDistance AverageSpeed MedianSpeed MinimumSpeed MaximumSpeed green 14.01 10.733333333333333 1.0 180.0 4.93 3.138213 0.16093400000000002 160.8857198 20.27 18.36007605633803 0.058884276857404216 104.60709999999999 yellow 14.43 11.283333333333333 1.0 180.0 4.88 2.735878 0.16093400000000002 160.8696264 18.73 16.444784279475982 0.05373422370617697 104.6071

In [0]:
q3c_result = spark.sql("""
SELECT 
  TaxiColor,
  PUBorough AS PickupBorough,
  DOBorough AS DropoffBorough,
  MONTH(COALESCE(lpep_pickup_datetime, tpep_pickup_datetime)) AS Month,
  DAYOFWEEK(COALESCE(lpep_pickup_datetime, tpep_pickup_datetime)) AS DayOfWeek,
  HOUR(COALESCE(lpep_pickup_datetime, tpep_pickup_datetime)) AS Hour,
  ROUND(AVG(total_amount), 2) AS AvgAmountPerTrip
FROM combined_view
GROUP BY TaxiColor, PickupBorough, DropoffBorough, Month, DayOfWeek, Hour
ORDER BY TaxiColor, PickupBorough, DropoffBorough, Month, DayOfWeek, Hour;
""")

q3c_result.write.option("header", "true").csv("/mnt/bde-2/Q3Canswer.csv")

q3c_result.show()



+---------+-------------+--------------+-----+---------+----+----------------+
|TaxiColor|PickupBorough|DropoffBorough|Month|DayOfWeek|Hour|AvgAmountPerTrip|
+---------+-------------+--------------+-----+---------+----+----------------+
|    green|        Bronx|         Bronx|    1|        1|   0|           10.92|
|    green|        Bronx|         Bronx|    1|        1|   1|           11.42|
|    green|        Bronx|         Bronx|    1|        1|   2|           11.32|
|    green|        Bronx|         Bronx|    1|        1|   3|           11.35|
|    green|        Bronx|         Bronx|    1|        1|   4|           11.82|
|    green|        Bronx|         Bronx|    1|        1|   5|           10.89|
|    green|        Bronx|         Bronx|    1|        1|   6|           11.39|
|    green|        Bronx|         Bronx|    1|        1|   7|           13.51|
|    green|        Bronx|         Bronx|    1|        1|   8|           14.57|
|    green|        Bronx|         Bronx|    1|      

In [0]:
%sql
WITH RankedResults AS (
  SELECT 
    TaxiColor,
    PUBorough AS PickupBorough,
    DOBorough AS DropoffBorough,
    MONTH(COALESCE(lpep_pickup_datetime, tpep_pickup_datetime)) AS Month,
    DAYOFWEEK(COALESCE(lpep_pickup_datetime, tpep_pickup_datetime)) AS DayOfWeek,
    HOUR(COALESCE(lpep_pickup_datetime, tpep_pickup_datetime)) AS Hour,
    
    COUNT(*) AS TotalTrips,
    ROUND(AVG(trip_distance * 1.60934), 2) AS AverageDistanceKM,
    ROUND(AVG(total_amount), 2) AS AvgAmountPerTrip,
    SUM(total_amount) AS TotalAmountPaid,

    ROW_NUMBER() OVER (PARTITION BY TaxiColor ORDER BY COUNT(*) DESC) as rn
  
  FROM combined_view
  GROUP BY TaxiColor, PickupBorough, DropoffBorough, Month, DayOfWeek, Hour
)

SELECT 
  TaxiColor,
  PickupBorough,
  DropoffBorough,
  Month,
  DayOfWeek,
  Hour,
  TotalTrips,
  AverageDistanceKM,
  AvgAmountPerTrip,
  TotalAmountPaid
FROM RankedResults
WHERE rn <= 5000
ORDER BY TaxiColor, PickupBorough, DropoffBorough, Month, DayOfWeek, Hour;


TaxiColor PickupBorough DropoffBorough Month DayOfWeek Hour TotalTrips AverageDistanceKM AvgAmountPerTrip TotalAmountPaid green Bronx Bronx 2 6 18 3531 3.89 13.36 47183.82999999938 green Bronx Bronx 3 2 8 3796 3.94 12.43 47167.04999999975 green Bronx Bronx 3 6 8 3539 4.33 13.05 46169.35000000003 green Bronx Bronx 3 6 17 3595 4.03 13.94 50096.609999999855 green Bronx Bronx 3 6 18 3520 3.87 13.01 45800.26999999982 green Brooklyn Brooklyn 1 1 0 21003 3.97 13.3 279289.17000000906 green Brooklyn Brooklyn 1 1 1 18958 4.02 13.22 250584.88000000763 green Brooklyn Brooklyn 1 1 2 16088 4.13 13.29 213877.36000000456 green Brooklyn Brooklyn 1 1 3 12958 4.19 13.31 172492.62000000168 green Brooklyn Brooklyn 1 1 4 8966 4.18 13.21 118451.76999999837 green Brooklyn Brooklyn 1 1 5 3677 4.34 13.29 48884.35999999973 green Brooklyn Brooklyn 1 1 9 4785 4.22 13.65 65334.36000000005 green Brooklyn Brooklyn 1 1 10 7058 3.84 12.94 91301.9799999993 green Brooklyn Brooklyn 1 1 11 8551 3.56 12.28 105010.83999999882 green Brooklyn Brooklyn 1 1 12 9730 3.64 12.62 122769.28999999844 green Brooklyn Brooklyn 1 1 13 11047 3.71 12.97 143245.4899999978 green Brooklyn Brooklyn 1 1 14 12030 3.62 12.75 153379.1499999975 green Brooklyn Brooklyn 1 1 15 13355 3.49 12.43 166052.34999999808 green Brooklyn Brooklyn 1 1 16 13768 3.48 12.39 170524.55999999814 green Brooklyn Brooklyn 1 1 17 13345 3.48 12.35 164786.67999999842 green Brooklyn Brooklyn 1 1 18 14218 3.47 12.15 172792.66999999853 green Brooklyn Brooklyn 1 1 19 13580 3.48 11.96 162443.00999999812 green Brooklyn Brooklyn 1 1 20 12524 3.51 12.36 154754.10999999847 green Brooklyn Brooklyn 1 1 21 11184 3.56 12.38 138420.64999999866 green Brooklyn Brooklyn 1 1 22 9930 3.76 12.59 125035.20999999897 green Brooklyn Brooklyn 1 1 23 8443 3.85 12.62 106580.55999999856 green Brooklyn Brooklyn 1 2 0 6778 3.87 12.64 85678.70999999865 green Brooklyn Brooklyn 1 2 1 4580 3.91 12.73 58287.44999999943 green Brooklyn Brooklyn 1 2 7 4414 4.53 15.34 67718.76999999981 green Brooklyn Brooklyn 1 2 8 7439 3.83 14.06 104628.67999999883 green Brooklyn Brooklyn 1 2 9 7900 3.73 13.61 107484.40999999859 green Brooklyn Brooklyn 1 2 10 7792 3.93 13.71 106824.42999999865 green Brooklyn Brooklyn 1 2 11 7873 3.92 13.54 106562.96999999863 green Brooklyn Brooklyn 1 2 12 7903 3.92 13.63 107721.30999999854 green Brooklyn Brooklyn 1 2 13 8442 3.96 13.84 116864.41999999818 green Brooklyn Brooklyn 1 2 14 9483 3.81 13.84 131252.8599999979 green Brooklyn Brooklyn 1 2 15 10604 3.68 13.76 145905.0599999974 green Brooklyn Brooklyn 1 2 16 11492 3.59 14.2 163165.6399999975 green Brooklyn Brooklyn 1 2 17 12785 3.36 13.63 174225.54999999912 green Brooklyn Brooklyn 1 2 18 14757 3.23 12.8 188942.9000000006 green Brooklyn Brooklyn 1 2 19 14477 3.16 12.16 176033.91000000035 green Brooklyn Brooklyn 1 2 20 12534 3.25 11.8 147866.3299999989 green Brooklyn Brooklyn 1 2 21 10705 3.37 11.91 127469.55999999869 green Brooklyn Brooklyn 1 2 22 8820 3.55 12.23 107866.25999999844 green Brooklyn Brooklyn 1 2 23 6733 3.66 12.26 82568.60999999881 green Brooklyn Brooklyn 1 3 0 4918 3.8 12.43 61143.869999999675 green Brooklyn Brooklyn 1 3 7 5361 4.37 15.27 81845.29999999942 green Brooklyn Brooklyn 1 3 8 8635 3.7 14.2 122596.38999999825 green Brooklyn Brooklyn 1 3 9 8872 3.74 13.95 123731.05999999808 green Brooklyn Brooklyn 1 3 10 8497 3.99 14.15 120246.98999999827 green Brooklyn Brooklyn 1 3 11 8257 4.09 14.31 118183.75999999834 green Brooklyn Brooklyn 1 3 12 8302 4.13 14.3 118689.72999999819 green Brooklyn Brooklyn 1 3 13 8537 4.04 14.05 119971.62999999813 green Brooklyn Brooklyn 1 3 14 9536 3.91 14.02 133670.4699999976 green Brooklyn Brooklyn 1 3 15 11085 3.79 13.99 155115.18999999712 green Brooklyn Brooklyn 1 3 16 11974 3.8 15.02 179848.95999999755 green Brooklyn Brooklyn 1 3 17 13697 3.43 14.24 195100.46999999986 green Brooklyn Brooklyn 1 3 18 16612 3.2 13.17 218785.8600000019 green Brooklyn Brooklyn 1 3 19 16668 3.16 12.48 207940.16000000114 green Brooklyn Brooklyn 1 3 20 15026 3.

In [0]:
%sql
WITH TipsData AS (
  SELECT 
    CASE 
      WHEN tip_amount > 0 THEN 1
      ELSE 0
    END AS ReceivedTip
  FROM combined_view
)

SELECT 
  ROUND(100 * SUM(ReceivedTip) / COUNT(*), 2) AS PercentageTripsWithTips
FROM TipsData;


PercentageTripsWithTips 63.6

In [0]:
%sql
WITH TipsAbove5 AS (
  SELECT 
    CASE 
      WHEN tip_amount >= 5 THEN 1
      ELSE 0
    END AS TipsAbove5
  FROM combined_view
  WHERE tip_amount > 0
)

SELECT 
  ROUND(100 * SUM(TipsAbove5) / COUNT(*), 2) AS PercentageTripsWithTipsAbove5
FROM TipsAbove5;


PercentageTripsWithTipsAbove5 12.23

In [0]:
%sql
WITH BinnedTrips AS (
  SELECT 
    CASE
      WHEN (UNIX_TIMESTAMP(lpep_dropoff_datetime) - UNIX_TIMESTAMP(lpep_pickup_datetime))/60.0 < 5 THEN 'Under 5 Mins'
      WHEN (UNIX_TIMESTAMP(lpep_dropoff_datetime) - UNIX_TIMESTAMP(lpep_pickup_datetime))/60.0 BETWEEN 5 AND 10 THEN '5 to 10 Mins'
      WHEN (UNIX_TIMESTAMP(lpep_dropoff_datetime) - UNIX_TIMESTAMP(lpep_pickup_datetime))/60.0 BETWEEN 10 AND 20 THEN '10 to 20 Mins'
      WHEN (UNIX_TIMESTAMP(lpep_dropoff_datetime) - UNIX_TIMESTAMP(lpep_pickup_datetime))/60.0 BETWEEN 20 AND 30 THEN '20 to 30 Mins'
      WHEN (UNIX_TIMESTAMP(lpep_dropoff_datetime) - UNIX_TIMESTAMP(lpep_pickup_datetime))/60.0 BETWEEN 30 AND 60 THEN '30 to 60 Mins'
      ELSE 'At least 60 Mins'
    END AS DurationBin,
    (trip_distance * 1.60934) AS DistanceKM,  -- Convert distance to km
    total_amount,
    (trip_distance * 1.60934) / ((UNIX_TIMESTAMP(lpep_dropoff_datetime) - UNIX_TIMESTAMP(lpep_pickup_datetime))/3600.0) AS SpeedKMH  -- Convert speed to km/h
  FROM combined_view
)

SELECT 
  DurationBin,
  ROUND(AVG(SpeedKMH), 2) AS AverageSpeedKMH,
  ROUND(AVG(DistanceKM / CASE WHEN total_amount = 0 THEN 1 ELSE total_amount END), 2) AS AvgDistancePerDollar
FROM BinnedTrips
GROUP BY DurationBin
ORDER BY DurationBin;


DurationBin AverageSpeedKMH AvgDistancePerDollar 10 to 20 Mins 20.82 0.33 20 to 30 Mins 22.56 0.39 30 to 60 Mins 22.65 0.47 5 to 10 Mins 18.5 0.25 At least 60 Mins 19.73 0.24 Under 5 Mins 19.74 0.18

In [0]:
%sql
WITH BinnedTrips AS (
  SELECT 
    CASE
      WHEN (UNIX_TIMESTAMP(lpep_dropoff_datetime) - UNIX_TIMESTAMP(lpep_pickup_datetime))/60.0 < 5 THEN 'Under 5 Mins'
      WHEN (UNIX_TIMESTAMP(lpep_dropoff_datetime) - UNIX_TIMESTAMP(lpep_pickup_datetime))/60.0 BETWEEN 5 AND 10 THEN '5 to 10 Mins'
      WHEN (UNIX_TIMESTAMP(lpep_dropoff_datetime) - UNIX_TIMESTAMP(lpep_pickup_datetime))/60.0 BETWEEN 10 AND 20 THEN '10 to 20 Mins'
      WHEN (UNIX_TIMESTAMP(lpep_dropoff_datetime) - UNIX_TIMESTAMP(lpep_pickup_datetime))/60.0 BETWEEN 20 AND 30 THEN '20 to 30 Mins'
      WHEN (UNIX_TIMESTAMP(lpep_dropoff_datetime) - UNIX_TIMESTAMP(lpep_pickup_datetime))/60.0 BETWEEN 30 AND 60 THEN '30 to 60 Mins'
      ELSE 'At least 60 Mins'
    END AS DurationBin,
    total_amount
  FROM combined_view
)

SELECT 
  DurationBin,
  ROUND(AVG(total_amount), 2) AS AverageFare,
  COUNT(*) AS TripCount,
  ROUND(AVG(total_amount) * COUNT(*), 2) AS EstimatedIncome
FROM BinnedTrips
GROUP BY DurationBin
ORDER BY EstimatedIncome DESC;


DurationBin AverageFare TripCount EstimatedIncome At least 60 Mins 17.17 653729118 1.122247112124E10 10 to 20 Mins 15.63 21429098 3.3493898919E8 20 to 30 Mins 25.36 7681865 1.9484203495E8 5 to 10 Mins 9.35 19867030 1.8575499563E8 30 to 60 Mins 38.64 4736223 1.8298628438E8 Under 5 Mins 6.57 9889870 6.498629591E7

In [0]:
from pyspark.sql import SparkSession
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.regression import LinearRegression, DecisionTreeRegressor
from pyspark.ml import Pipeline
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.sql.functions import col, lit, month, year

# Initialize Spark session
spark = SparkSession.builder.appName("Taxi Fare Prediction").getOrCreate()

# Read the dataset from the Parquet file
parquet_path = "/mnt/bde-2/combined_data_cleaned3.parquet"
df = spark.read.parquet(parquet_path)

# Compute trip duration in seconds
df = df.withColumn("trip_duration", (col("tpep_dropoff_datetime").cast("long") - col("tpep_pickup_datetime").cast("long")))

# Fill null values with defaults
default_values = {
    "trip_distance": 0.0,
    "passenger_count": 1,
    "RatecodeID": 1,
    "trip_duration": 0
}
df = df.fillna(default_values)

# Separate data for test set before sampling
test_df = df.filter((year("tpep_pickup_datetime") == 2022) & (month("tpep_pickup_datetime") >= 10))

# Sample data for training and validation
df_sampled = df.sample(False, 0.6, seed=42)

# Split the sampled data into training and validation
train_df, validation_df = df_sampled.randomSplit([0.8, 0.2], seed=42)

# Load the Q3C answer from the CSV file
q3c_df = spark.read.csv("/mnt/bde-2/Q3Canswer.csv", header=True, inferSchema=True)

# Compute the overall average fare from the AvgAmountPerTrip column
overall_average_fare_q3c = q3c_df.agg({"AvgAmountPerTrip": "avg"}).collect()[0][0]

# Use the overall average fare for predictions
baseline_predictions_validation = validation_df.withColumn("prediction", lit(overall_average_fare_q3c))


evaluator = RegressionEvaluator(labelCol="total_amount", predictionCol="prediction", metricName="rmse")
baseline_rmse_validation = evaluator.evaluate(baseline_predictions_validation)
print(f"Baseline Model RMSE on Validation Data: {baseline_rmse_validation:.2f}")

# Vectorize the features without the location IDs
features = ["trip_distance", "passenger_count", "RatecodeID", "trip_duration"]
vector_assembler = VectorAssembler(inputCols=features, outputCol="features", handleInvalid="keep")

# Linear Regression Model
lr = LinearRegression(featuresCol="features", labelCol="total_amount")
pipeline = Pipeline(stages=[vector_assembler, lr])
lr_model = pipeline.fit(train_df)
lr_predictions = lr_model.transform(validation_df)
lr_rmse = evaluator.evaluate(lr_predictions)
print(f"Linear Regression Model RMSE on Validation Data: {lr_rmse:.2f}")

lr_predictions_test = lr_model.transform(test_df)
lr_rmse_test = evaluator.evaluate(lr_predictions_test)
print(f"Linear Regression Model RMSE on Test Data: {lr_rmse_test:.2f}")

# Baseline Model for Test Data
baseline_predictions_test = test_df.withColumn("prediction", lit(average_fare_q3c))
test_baseline_rmse = evaluator.evaluate(baseline_predictions_test)
print(f"Baseline Model RMSE on Test Data: {test_baseline_rmse:.2f}")


Baseline Model RMSE on Validation Data: 130.88
Linear Regression Model RMSE on Validation Data: 127.22
Linear Regression Model RMSE on Test Data: 7.19


---------------------------------------------------------------------------
IllegalArgumentException                  Traceback (most recent call last)
File <command-3989595250661445>, line 68
     66 # Baseline Model for Test Data
     67 baseline_predictions_test = test_df.withColumn("prediction", lit(average_fare_q3c))
---> 68 test_baseline_rmse = evaluator.evaluate(baseline_predictions_test)
     69 print(f"Baseline Model RMSE on Test Data: {test_baseline_rmse:.2f}")

File /databricks/python/lib/python3.10/site-packages/mlflow/utils/autologging_utils/safety.py:552, in safe_patch.<locals>.safe_patch_function(*args, **kwargs)
    550     patch_function.call(call_original, *args, **kwargs)
    551 else:
--> 552     patch_function(call_original, *args, **kwargs)
    554 session.state = "succeeded"
    556 try_log_autologging_event(
    557     AutologgingEventLogger.get_logger().log_patch_function_success,
    558     session,
   (...)
    562     kwargs,
    563 )

File /databricks/py

In [0]:
# Use the overall average fare from Q3C for predictions on the test set
baseline_predictions_test = test_df.withColumn("prediction", lit(overall_average_fare_q3c).cast("double"))

# Compute RMSE for the baseline model on the test set
test_baseline_rmse = evaluator.evaluate(baseline_predictions_test)
print(f"Baseline Model RMSE on Test Data: {test_baseline_rmse:.2f}")



Baseline Model RMSE on Test Data: 28.24
